In [ ]:
import pandas as pd
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
from collections import OrderedDict
from time import time

import numpy as np
import scipy as sp
import pandas as pd

from scipy.optimize import fmin_powell
from scipy import integrate
from scipy import linalg

from sklearn.preprocessing import normalize
from sklearn import linear_model
from sklearn.exceptions import ConvergenceWarning

np.set_printoptions(precision=6, suppress=True)

sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
figsize = (15,8)
legend_fontsize = 16

from matplotlib import rc
rc('font',**{'family':'sans-serif'})
rc('text', usetex=True)
rc('text.latex',preamble=r'\usepackage[utf8]{inputenc}')
rc('text.latex',preamble=r'\usepackage[russian]{babel}')
rc('axes', **{'titlesize': '16', 'labelsize': '16'})
rc('legend', **{'fontsize': '16'})
rc('figure', **{'dpi' : 300})

## Определяем регрессию как обычно

In [ ]:
## Исходная функция
orig = lambda x : np.sin(2*x)

## X-координаты точек данных
# xd = np.arange(-1.5, 2, 7/60)
xd = np.array([-3, -2, -1, -0.5, 0, 0.5, 1, 1.5, 2.5, 3, 4]) / 2
# xd = np.array([-3, -2, -1, -0.5, 0, 0.5, 1, 1.5, 2.5, 3, 4]) / 2
num_points = len(xd)

## Данные
data = orig(xd) + np.random.normal(0, .25, num_points)

## Для рисования
xs = np.arange(xd[0]-1.5, xd[-1]+1.5, 0.01)

## Обучаем модель с регуляризацией
def train_model(xs, ys, alpha=0, use_lasso=False):
    if alpha == 0:
        return linear_model.LinearRegression(fit_intercept=True).fit( xs, ys )
    else:
        if use_lasso:
            return linear_model.Lasso(alpha=alpha, fit_intercept=True).fit( xs, ys )
        else:
            return linear_model.Ridge(alpha=alpha, fit_intercept=True).fit( xs, ys )

In [ ]:
## Выделение полиномиальных признаков
xs_d = np.vstack([xs ** i for i in range(1, num_points+1)]).transpose()
xd_d = np.vstack([xd ** i for i in range(1, num_points+1)]).transpose()

## Какие степени многочлена будем обучать и рисовать
set_of_powers = [ 1, 3, 10 ]

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-2, 2))
ax.scatter(xd, data, marker='*', s=120)
ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")

for d in set_of_powers:
    if d == 0:
        print(np.mean(data))
        ax.hlines(np.mean(data), xmin=xs[0], xmax=xs[-1], label="$d=0$", linestyle="dashed")
    else:
        cur_model = train_model( xd_d[:, :d], data, alpha=0.0 )
        print(cur_model.coef_)
        ax.plot(xs, cur_model.predict( xs_d[:, :d] ), linewidth=2, label="$d=%d$" % d)

ax.legend(loc="lower center", fontsize=legend_fontsize)

## Эмпирический Байес

In [ ]:
## Порождает матрицу признаков в явном виде
def get_X(d):
    return np.hstack([np.ones(xd_d[:, :d].shape[0]).reshape(-1, 1), xd_d[:, :d]])

## Выдаёт оценку дисперсии шума по текущей гипотезе максимального правдоподобия
def linregr_sigma(X, y):
    N = X.shape[0]
    XtX = X.T.dot(X)
    mu = np.linalg.inv(XtX).dot(X.T).dot(data)
    preds = X.dot(mu)
    sigma2 = (np.sum((preds-data)**2) / N)
    return mu, sigma2

In [ ]:
def bayesian_update(mu, Sigma, X, t, beta=4):
    Sigma_inv = np.linalg.inv(Sigma)
    Sigma_n_inv = Sigma_inv + beta * X.T.dot(X)
    Sigma_n = np.linalg.inv(Sigma_n_inv)
    mu_n = Sigma_n.dot( Sigma_inv.dot(mu.T) + beta * X.T.dot(t) )
    return mu_n, Sigma_n

def log_marginal_likelihood(X, t, alpha, beta):
    N, M = X.shape
    mu, sigma = bayesian_update(np.zeros(M), (1/alpha) * np.identity(M), X, t, beta=beta)
    A = np.linalg.inv(sigma)
    return 0.5 * ( M * np.log(alpha) + N * np.log(beta) - \
                  np.log(np.linalg.det(A)) - \
                  beta * np.sum((t - X.dot(mu)) ** 2) - \
                  alpha * np.sum(mu ** 2) - \
                  N * np.log(2 * np.pi) )

def lr_log_marginal(xx, t, d, alpha=0.001, beta=4):
    return log_marginal_likelihood(get_X(d), t, alpha, beta)

In [ ]:
lr_evid = [ lr_log_marginal(xd_d, data, d, alpha=0.005) for d in range(1, 12)]
lr_evid2 = [ lr_log_marginal(xd_d, data, d, alpha=0.01) for d in range(1, 12)]
lr_evid3 = [ lr_log_marginal(xd_d, data, d, alpha=0.1) for d in range(1, 12)]
lr_evid4 = [ lr_log_marginal(xd_d, data, d, alpha=1) for d in range(1, 12)]

In [ ]:
N, dmax = data.shape[0], 12
lrs = [ linregr_sigma( get_X(d), data ) for d in range(1, dmax) ]

In [ ]:
fig = plt.figure(figsize=(12, 5))
ax = fig.add_subplot(111)
ax.plot(range(1, 12), lr_evid, marker='.', label=r'$\alpha=0.005$')
ax.plot(range(1, 12), lr_evid2, marker='.', label=r'$\alpha=0.01$')
ax.plot(range(1, 12), lr_evid3, marker='.', label=r'$\alpha=0.1$')
ax.plot(range(1, 12), lr_evid4, marker='.', label=r'$\alpha=1$')
ax.set_xlim((1, 11))
ax.legend(fontsize=14)

In [ ]:
alphas = np.logspace(-5, 5, 50)

d = 3
evids = [lr_log_marginal(xd_d, data, d, alpha=a, beta=4) for a in alphas]
evids2 = [lr_log_marginal(xd_d, data, d, alpha=a, beta=1) for a in alphas]
evids3 = [lr_log_marginal(xd_d, data, d, alpha=a, beta=10) for a in alphas]

d = 10
evids4 = [lr_log_marginal(xd_d, data, d, alpha=a, beta=4) for a in alphas]
evids5 = [lr_log_marginal(xd_d, data, d, alpha=a, beta=1) for a in alphas]
evids6 = [lr_log_marginal(xd_d, data, d, alpha=a, beta=10) for a in alphas]

fig = plt.figure(figsize=(12, 5))
ax = fig.add_subplot(111)
ax.set_xscale('log')
ax.plot(alphas, evids, label=r'$d=3$, $\beta=4$')
ax.plot(alphas, evids2, label=r'$d=3$, $\beta=1$')
ax.plot(alphas, evids3, label=r'$d=3$, $\beta=10$')
ax.plot(alphas, evids4, label=r'$d=10$, $\beta=4$', c=palette[0], linestyle='--')
ax.plot(alphas, evids5, label=r'$d=10$, $\beta=1$', c=palette[1], linestyle='--')
ax.plot(alphas, evids6, label=r'$d=10$, $\beta=10$', c=palette[2], linestyle='--')
ax.set_xlim((10**(-5), 10**5))
ax.set_ylim((-50, -10))
ax.legend(fontsize=14, ncol=2)

In [ ]:
## Одна итерация эмпирического Байеса
def empirical_iteration(X, t, XtX, XtT, lambdas, alpha, beta):
    N, d = X.shape
    cur_lambdas = beta * lambdas
    gamma = np.sum(cur_lambdas / (alpha + cur_lambdas))
    A = beta * XtX + alpha * np.identity(d)
    mu = beta * np.linalg.inv(A).dot(XtT)
    a = gamma / np.sum(mu ** 2)
    b = (N - gamma) / np.sum( (t - X.dot(mu)) ** 2)
    return a, b

## Обучаем эмпирический Байес
def fit_eb(X, t, max_iter=400, eps=0.0001):
    XtX = X.T.dot(X)
    XtT = X.T.dot(t)
    lambdas = np.linalg.eigvalsh(XtX)
    alpha_0, beta_0 = 1, 1
    alpha, beta = [alpha_0], [beta_0]
    logmargs = [log_marginal_likelihood(X, t, alpha=alpha_0, beta=beta_0)]
    for _ in range(max_iter):
        a, b = empirical_iteration(X, t, XtX, XtT, lambdas, alpha[-1], beta[-1])
        alpha.append(a)
        beta.append(b)
        logmargs.append(log_marginal_likelihood(X, t, alpha=a, beta=b))
        if np.isclose(alpha[-1], alpha[-2], eps) and np.isclose(beta[-1], beta[-2], eps):
            break
    return alpha, beta, logmargs

In [ ]:
d1, d2 = 3, 4
alphas, betas, lms = fit_eb(get_X(d1), data)
alphas2, betas2, lms2 = fit_eb(get_X(d2), data)

In [ ]:
alphas2

In [ ]:
aas = np.logspace(-5, 5, 100)

evids = [lr_log_marginal(xd_d, data, d1, alpha=a, beta=betas[-1]) for a in aas]
evids2 = [lr_log_marginal(xd_d, data, d2, alpha=a, beta=betas2[-1]) for a in aas]

fig = plt.figure(figsize=(12, 5))
ax = fig.add_subplot(111)
ax.set_xscale('log')
ax.plot(aas, evids, label=r'$d=%d$, $\beta=%.4f$' % (d1, betas[-1]))
ax.vlines(alphas[-1], -70, lr_log_marginal(xd_d, data, d1, alpha=alphas[-1], beta=betas[-1]), linestyles='--')
ax.text(alphas[-1]+.2, -40, r'$\mathbf{\alpha=%.4f}$' % alphas[-1], rotation=90, fontsize=16, color=palette[0], horizontalalignment='left')
ax.plot(aas, evids2, label=r'$d=%d$, $\beta=%.4f$' % (d2, betas2[-1]))
ax.vlines(alphas2[-1], -70, lr_log_marginal(xd_d, data, d2, alpha=alphas2[-1], beta=betas2[-1]), linestyles='--', colors=palette[1])
ax.text(alphas2[-1]-.1, -40, r'$\mathbf{\alpha=%.4f}$' % alphas2[-1], rotation=90, fontsize=16, color=palette[1], horizontalalignment='right')
ax.set_xlim((10**(-5), 10**5))
ax.set_ylim((-50, -10))
ax.legend(fontsize=14)

## Выбор модели в полиномиальной регрессии

In [ ]:
N, dmax = data.shape[0], 12
lrs = [ linregr_sigma( get_X(d), data ) for d in range(1, dmax) ]

In [ ]:
def logL(lr, N, d):
    return -.5*N*(np.log(2*np.pi) + np.log(lr[1])+1)

def BIC(lr, N, d):
    return N*(np.log(2*np.pi) + np.log(lr[1]) + 1) + np.log(N)*(d+2)

def AIC(lr, N, d):
    return N*(np.log(2*np.pi) + np.log(lr[1]) + 1) + 2*(d+2)

In [ ]:
ds = np.arange(1, dmax)
logLs = [logL(lrs[d-1], N, d) for d in ds]
AICs = [AIC(lrs[d-1], N, d) for d in ds]
BICs = [BIC(lrs[d-1], N, d) for d in ds]

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((1, dmax-2))
ax.set_ylim((-50, 50))
ax.plot(ds, logLs, label='Логарифм правдоподобия', linewidth=2, marker='.', markersize=10)
ax.plot(ds, AICs, label="AIC", linewidth=2, marker='.', markersize=10)
ax.plot(ds, BICs, label="BIC", linewidth=2, marker='.', markersize=10)
ax.legend(fontsize=legend_fontsize)